In [1]:
'''
given the ohlcv, TA, what will the high be within the first 15 minutes of market open


'''

'\ngiven the ohlcv, TA, what will the high be within the first 15 minutes of market open\n\nget more of the 1 minute tickers\n1. organize the data into days\n\n'

In [26]:
import pandas as pd
import datetime as dt
from pandas.tseries.offsets import MonthEnd
import requests
import numpy as np
import random
import os
import torch
from torch.utils.data import Dataset
from skimage import io
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
import torchvision
from torch.utils.data import DataLoader


In [28]:
#adds technical indicators to the dataframe
def all_tech_ind(df):
        
    #RSI and some MA    
    df['avg_volume'] = df['volume'].rolling(window=20).mean()
    df['MA200'] = df['close'].rolling(window=200).mean()
    df['price change'] = df['close'].pct_change()
    df['Upmove'] = df['price change'].apply(lambda x: x if x > 0 else 0)
    df['Downmove'] = df['price change'].apply(lambda x: abs(x) if x < 0 else 0)
    df['avg up'] = df['Upmove'].ewm(span=19).mean()
    df['avg down'] = df['Downmove'].ewm(span=19).mean()

    
    #MACD for Trend inidicators
    # alternate macd settings, fast 8, slow 21, MACD len 5
    df['MA9'] = df['close'].rolling(window=9).mean()
    df['Signaline'] = df['close'].ewm(span=9,adjust=False).mean()
    df['emaslow'] = df['close'].ewm(span=26,adjust=False).mean()
    df['emafast'] = df['close'].ewm(span=12,adjust=False).mean()
    df['MACD'] = df['emafast'] - df['emaslow']

    
    #bollinger bands for volatility inidicators
    df['MA20'] = df['close'].rolling(window=20).mean()
    df['rstd'] = df['close'].rolling(window=20).std()
    df['upper_band'] = df['MA20'] + 2 * df['rstd']
    df['lower_band'] = df['MA20'] - 2 * df['rstd']
    
    #the rest of RSI  for momentum inidicators
    df = df.dropna()
    df['RS'] = df['avg up']/df['avg down']
    df['RSI'] = df['RS'].apply(lambda x: 100-(100/(x+1)))
    
    df['vwap'] = (df['volume']*df['close']).cumsum() / df['volume'].cumsum()
    
    return df

In [ ]:
#create a bunch of minute candlestick files
directory = 'minute_candlesticks/'
for filename in os.listdir(directory):
    try:
        name = filename.replace(".csv","")
        date_i_picked = int(dt.datetime(2016,1,1).timestamp()) * 1000

        endpoint = f'https://api.tdameritrade.com/v1/marketdata/{name}/pricehistory'

        payload = {
            'apikey': nonyourbusiness,
            'periodType':'year',
            'period':'5',
            'frequencyType':'daily',
            'frequency': '1',
            'startDate':date_i_picked,
            'needExtendedHoursData':'true'

        }

        content = requests.get(url=endpoint, params=payload)

        data = content.json()

        for i in data['candles']:
            i['human_dt'] = dt.datetime.fromtimestamp(i['datetime']/1000).strftime('%Y-%m-%d %H:%M:%S')

        df = pd.DataFrame(data['candles'])
        ta_df = all_tech_ind(df)
        ta_df.to_csv(f'day_candlesticks/{name}.csv')
        print(f'{name} saved and it was {len(ta_df)} long')
    except:
        print(f'{name} didnt work')

In [ ]:
#add to minutes if needed
count = 0
directory = 'minute_candlesticks/'
for filename in os.listdir(directory):
    try:

        count+=1
        ticker = filename.replace('.csv','')

        df = pd.read_csv(f'minute_candlesticks/{ticker}.csv')

        old_df = df[['open', 'high','low', 'close','volume', 'datetime','human_dt']]
        oldlen = len(old_df)

        last_dt = int(old_df.tail(1)['datetime'])

        endpoint = f'https://api.tdameritrade.com/v1/marketdata/{ticker}/pricehistory'

        payload = {
            'apikey': nonyourbusiness,
            'periodType':'day',
            'period':'1',
            'frequencyType':'minute',
            'frequency': '1',
            'startDate':last_dt,
            'needExtendedHoursData':'true'

        }

        content = requests.get(url=endpoint, params=payload)

        data = content.json()

        for i in data['candles']:
            i['human_dt'] = dt.datetime.fromtimestamp(i['datetime']/1000).strftime('%Y-%m-%d %H:%M:%S')

        new_df = pd.DataFrame(data['candles'])
        combined = old_df.append(new_df,ignore_index=True)

        combined = combined.drop_duplicates()
        newlen = len(combined)
        added = newlen-oldlen
        combined.to_csv(f'minute_candlesticks/{ticker}.csv')
        print(count)
        print(f'{ticker} added {added} new minutes')
    except:
        print(f'{ticker}-------------------didnt work')

In [25]:
count = 0
tick = pd.read_csv(f'5min/AAPL.csv')
indices = []
for index, row in tick.iterrows():
    if '04:00:00' in row['human_dt']:
        if '09:25' in tick.iloc[index+65]['human_dt']:
            count+=1
print(count)


61


In [33]:
#process whole 5 minute csv files into individual premarket files, calculate the label, save info in master df
count = 0
directory = '5min/'
for filename in os.listdir(directory):
    tick = pd.read_csv(f'{directory}{filename}')
    indices = []
    for index, row in tick.iterrows():
        if '04:00:00' in row['human_dt']:
            try:
                if '09:25' in tick.iloc[index+65]['human_dt']:
                    indices.append([index,index+65,index+80])
            except:
                print('out of range')
    tick = all_tech_ind(tick)

    if len(indices) > 0:
        print(f'in {filename}')
        for i in indices:
            try:
                premarket = tick.iloc[i[0]:i[1]]
                window = tick.iloc[i[1]:i[2]]

                date = tick.iloc[i[0]]['human_dt'].split(' ')[0]

                high = window['high'].max()

                close = float(premarket.tail(1)['close'])

                change = round((high-close)/close*100)

                if change == 0:
                    labels = 2
                elif change < -5:
                    labels = 0
                elif change < 0:
                    labels = 1
                elif change > 5:
                    labels = 4
                elif change > 0:
                    labels = 3

                count+=1
                premarket = premarket.drop(['human_dt','datetime','Unnamed: 0'],axis=1)

                name = f'5min_premarket/{date}{filename}'
                print(name)
                premarket.to_csv(name)
                new_df = pd.DataFrame([[name,labels]], columns = ['location', 'label'])
                df = df.append(new_df,ignore_index=True)
            except:
                print(f'{filename}-------------------didnt work')
    print(f'processed {filename}, {count} days total')


/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

processed MU.csv, 0 days total


/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

processed PLYA.csv, 0 days total


/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

...

/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

processed TMCI.csv, 2744 days total


/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

processed KLR.csv, 2744 days total
processed J.csv, 2744 days total


/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/kyle/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveat

In [13]:
count = 0
directory = 'minute_candlesticks/'
for filename in os.listdir(directory):
    tick = pd.read_csv(f'{directory}{filename}')
    indices = []
    for index, row in tick.iterrows():
        if '04:00:00' in row['human_dt']:
            try:
                if '09:2' in tick.iloc[index+325]['human_dt']:
                    indices.append([index,index+325,index+340])
            except:
                print('out of range')
    tick = all_tech_ind(tick)

    if len(indices) > 0:
        print(f'in {filename}')
        for i in indices:
            premarket = tick.iloc[i[0]:i[1]]
            window = tick.iloc[i[1]:i[2]]

            date = tick.iloc[i[0]]['human_dt'].split(' ')[0]

            high = window['high'].max()

            close = float(premarket.tail(1)['close'])

            change = round((high-close)/close*100)

            if change == 0:
                labels = 2
            elif change < -5:
                labels = 0
            elif change < 0:
                labels = 1
            elif change > 5:
                labels = 4
            elif change > 0:
                labels = 3

            count+=1
            premarket = premarket.drop(['human_dt','datetime','Unnamed: 0'],axis=1)

            name = f'densenet_premarket/{date}{filename}'
            print(name)
            premarket.to_csv(name)
            new_df = pd.DataFrame([[name,labels]], columns = ['location', 'label'])
            df = df.append(new_df,ignore_index=True)
    print(f'processed {filename}')


processed MU.csv
processed PLYA.csv
processed HII.csv
processed QELL.csv
processed AUTL.csv
processed ECOL.csv
processed SIEN.csv
processed TFFP.csv
processed PPT.csv
processed BXMT.csv
processed ZDGE.csv
processed RICE.csv
processed CARG.csv
processed CHTR.csv
processed REED.csv
processed GIII.csv
processed ECOM.csv
processed STXS.csv
processed HRZN.csv
processed PFN.csv
processed SGRP.csv
processed AIR.csv
processed ALLY-A.csv
processed ORGO.csv
processed UMBF.csv
processed AVAV.csv
processed RLGY.csv
processed TEO.csv
processed LILA.csv
processed LPLA.csv
processed R.csv
processed RYTM.csv
processed CANG.csv
processed UPLD.csv
processed EPC.csv
processed LMPX.csv
processed MNRL.csv
processed SLRC.csv
processed RXN.csv
processed CNSL.csv
processed CAG.csv
processed VTR.csv
processed CATB.csv
processed SRRK.csv
processed MMM.csv
processed CTRE.csv
processed CHEK.csv
processed AXDX.csv
processed PHR.csv
processed HAIN.csv
processed OIS.csv
processed VVOS.csv
processed MEI.csv
processed

processed JBGS.csv
processed BAX.csv
processed BECN.csv
processed NET.csv
processed NKTR.csv
processed MRNA.csv
processed ELYS.csv
in EQOS.csv
densenet_premarket/2021-05-10EQOS.csv
processed EQOS.csv
processed UTHR.csv
processed CYH.csv
processed CFR.csv
processed ZEPP.csv
processed CLI.csv
processed BIGC.csv
processed COMM.csv
processed MTL.csv
processed VAL.csv
processed FPI.csv
processed WHF.csv
processed CNCE.csv
processed ADX.csv
processed PRAA.csv
processed MGPI.csv
processed RAPT.csv
processed AWH.csv
processed CSX.csv
in CLOV.csv
densenet_premarket/2021-06-08CLOV.csv
densenet_premarket/2021-06-09CLOV.csv
densenet_premarket/2021-06-10CLOV.csv
processed CLOV.csv
processed DBI.csv
processed BCX.csv
processed ALUS.csv
processed MMYT.csv
processed FUV.csv
processed SLNO.csv
processed BGB.csv
processed NOMD.csv
processed FRG.csv
processed KNDI.csv
processed RYAM.csv
processed ITCI.csv
processed LAZR.csv
processed ASPS.csv
processed EQT.csv
processed MLSS.csv
processed ETRN.csv
proces

processed PFGC.csv
processed TOWN.csv
processed VIRI.csv
processed UPWK.csv
processed AMSWA.csv
processed UTSI.csv
processed DNMR.csv
processed USNA.csv
processed BLE.csv
processed ZIM.csv
processed CELH.csv
processed DUK.csv
processed GPC.csv
processed ZG.csv
processed GILD.csv
processed CERE.csv
processed GLAQ.csv
processed ELS.csv
processed FYBR.csv
processed IART.csv
processed USAK.csv
processed EDN.csv
processed DTST.csv
processed VOD.csv
processed HBIO.csv
processed CRNX.csv
processed CIEN.csv
processed TGP.csv
processed SHIP.csv
processed ELA.csv
processed GFI.csv
processed JOE.csv
processed CPB.csv
processed QEP.csv
processed AAL.csv
processed LTHM.csv
processed HAAC.csv
processed AXAS.csv
processed VUZI.csv
processed TMST.csv
processed PAVM.csv
processed NVRO.csv
processed SNMP.csv
processed AIV.csv
processed AVGR.csv
processed GHL.csv
processed CEIX.csv
processed RSG.csv
processed RBLX.csv
processed FC.csv
processed APP.csv
processed ADES.csv
processed BHAT.csv
processed IPOF

processed UFPI.csv
processed VISL.csv
processed GTLS.csv
processed ERJ.csv
processed SFNC.csv
processed AAT.csv
processed AXON.csv
processed ACEV.csv
processed GPN.csv
processed EPAY.csv
processed GBCI.csv
processed UWMC.csv
processed CGEN.csv
processed PFIE.csv
processed YRD.csv
processed USFD.csv
out of range
processed LYG.csv
processed IGR.csv
processed AM.csv
processed TLRY.csv
processed USPH.csv
processed MTZ.csv
processed MMX.csv
processed ORA.csv
processed STT.csv
processed ESI.csv
processed GMLP.csv
processed RDWR.csv
processed CNA.csv
processed ATOM.csv
processed PRAH.csv
processed CSTL.csv
processed SWM.csv
processed DVAX.csv
processed FMX.csv
processed EOG.csv
processed MDB.csv
processed JBHT.csv
processed VERO.csv
processed BCC.csv
processed MLCO.csv
processed ZUMZ.csv
processed DCT.csv
processed DEN.csv
processed SBS.csv
processed GSX.csv
processed JOB.csv
processed YELP.csv
processed WBAI.csv
processed USAU.csv
processed WTTR.csv
processed TAL.csv
processed MOS.csv
proces

processed FEN.csv
processed UAMY.csv
processed NEWT.csv
processed GAN.csv
processed RFP.csv
processed ATNM.csv
processed PLAY.csv
processed MUI.csv
processed ZOM.csv
processed SLQT.csv
processed AVEO.csv
processed VBLT.csv
processed SSD.csv
processed SPR.csv
processed LEVI.csv
processed HOME.csv
processed LZB.csv
processed TCRR.csv
processed EGOV.csv
processed AJAX.csv
processed APO.csv
processed SNAP.csv
processed SRG.csv
processed FMBI.csv
processed TBI.csv
processed THCA.csv
processed CHRW.csv
processed PTY.csv
processed ARVN.csv
processed NIO.csv
processed PEGA.csv
processed WNC.csv
processed SYF.csv
processed JBT.csv
processed MTLS.csv
processed OBSV.csv
processed CLVS.csv
processed INGN.csv
processed SMG.csv
processed VTAQ.csv
processed LAIX.csv
processed FLT.csv
processed ANET.csv
processed DSAC.csv
processed CTS.csv
processed OII.csv
processed SSL.csv
processed SPRQ.csv
processed DPG.csv
processed FARO.csv
processed METC.csv
processed AHT.csv
processed PHIO.csv
processed HJLI.c

...

processed ALLT.csv
processed REKR.csv
processed JBI.csv
processed JUPW.csv
processed RAMP.csv
processed LSI.csv
processed LCTX.csv
processed GLPI.csv
processed CMBM.csv
processed EXTR.csv
processed SDH.csv
processed ARRY.csv
processed EXG.csv
processed BOOT.csv
processed ALTU.csv
processed UVV.csv
processed PRG.csv
processed GTY.csv
processed RRC.csv
processed ASMB.csv
processed VECO.csv
processed GSL.csv
processed NEW.csv
processed EYEN.csv
processed BDTX.csv
processed LPSN.csv
processed RTX.csv
processed PTMN.csv
processed AGC.csv
processed SNCR.csv
processed RMTI.csv
out of range
processed OCG.csv
processed USCR.csv
processed DG.csv
processed GGT.csv
processed GKOS.csv
processed TBBK.csv
processed FINV.csv
processed ADTX.csv
processed EARS.csv
processed FEI.csv
processed SONM.csv
processed WD.csv
processed EVBG.csv
processed RFL.csv
processed MDLY.csv
processed LU.csv
processed DDS.csv
processed E.csv
processed TX.csv
processed LATN.csv
processed CORE.csv
processed ASRV.csv
processe

processed ROAD.csv
processed ABR.csv
processed CTT.csv
processed BBIG.csv
processed FCAC.csv
processed BHP.csv
processed SPSC.csv
processed MUJ.csv
processed MSN.csv
processed PDD.csv
processed JKHY.csv
processed CTAC.csv
processed OWL.csv
processed BDN.csv
processed CPE.csv
processed NTRA.csv
processed WRB.csv
processed ACRE.csv
processed SHO.csv
processed WMG.csv
processed KDMN.csv
processed ARKO.csv
processed TLK.csv
processed JRO.csv
processed LLIT.csv
processed HUDI.csv
processed DCI.csv
processed RIV.csv
processed SHW.csv
processed PJT.csv
processed PDSB.csv
processed SCYX.csv
processed BRK.B.csv
processed MYTE.csv
processed DRH.csv
processed NOAC.csv
processed BRX.csv
out of range
processed DUO.csv
processed IIAC.csv
processed TYME.csv
processed DGNS.csv
processed APM.csv
processed FSI.csv
processed AAP.csv
in AEMD.csv
densenet_premarket/2021-06-09AEMD.csv
processed AEMD.csv
processed ALRM.csv
processed CNTY.csv
processed CHKP.csv
processed HLX.csv
processed WOR.csv
processed DE

in SPCE.csv
densenet_premarket/2021-05-24SPCE.csv
processed SPCE.csv
processed RLH.csv
processed MFH.csv
processed NXST.csv
processed DAL.csv
processed DAIO.csv
processed NSA.csv
processed GCI.csv
processed ASR.csv
processed PED.csv
processed MRKR.csv
in MRIN.csv
densenet_premarket/2021-06-24MRIN.csv
densenet_premarket/2021-06-29MRIN.csv
processed MRIN.csv
processed ZYNE.csv
processed AVAH.csv
processed WLL.csv
processed COG.csv
processed RENN.csv
processed TLMD.csv
processed WAL.csv
processed AMCR.csv
processed CTXR.csv
processed THS.csv
processed KALV.csv
processed FORM.csv
processed COLD.csv
processed CYCC.csv
processed YQ.csv
processed MCY.csv
processed EGAN.csv
processed XPEV.csv
processed WLKP.csv
processed RAIN.csv
processed LSXMA.csv
in SNPR.csv
densenet_premarket/2021-06-28SNPR.csv
processed SNPR.csv
processed FUBO.csv
processed HUIZ.csv
processed MUDS.csv
processed MAS.csv
processed MASS.csv
processed ABCL.csv
processed LADR.csv
processed CWH.csv
processed KELYA.csv
processed

processed MRSN.csv
processed CHNG.csv
processed ROIC.csv
processed PRDO.csv
processed KERN.csv
processed NLTX.csv
processed NS.csv
processed STKS.csv
processed KRO.csv
processed FOXA.csv
processed NFLX.csv
processed DCRN.csv
processed SCOR.csv
processed SONA.csv
processed QH.csv
processed TGA.csv
processed BRN.csv
processed ADNT.csv
processed CHUY.csv
processed TRIT.csv
processed MOMO.csv
processed ARWR.csv
processed INSP.csv
processed DOV.csv
processed SSP.csv
processed AMP.csv
processed NVTA.csv
processed SPWH.csv
processed IBM.csv
processed AUVI.csv
processed FSKR.csv
processed SWTX.csv
processed INSW.csv
processed CMLF.csv
processed IR.csv
processed LNDC.csv
processed TEAM.csv
processed CLDX.csv
processed SWX.csv
processed MCK.csv
processed GSAH.csv
processed IPGP.csv
processed VRSK.csv
processed SITE.csv
processed VNE.csv
processed ATRA.csv
processed RMGCU.csv
processed MOGU.csv
processed PHG.csv
processed INSG.csv
processed PB.csv
processed LBTYA.csv
processed CNC.csv
processed C

processed NBHC.csv
processed NWE.csv
processed JEF.csv
processed EBET.csv
processed FBK.csv
processed CTLP.csv
processed NMRD.csv
processed MTBC.csv
processed NINE.csv
processed EHTH.csv
processed MMU.csv
processed CLH.csv
processed PSFE.csv
processed NEXI.csv
processed CNX.csv
processed ZUO.csv
processed NVO.csv
processed SEMR.csv
processed CI.csv
processed NCMI.csv
processed WLK.csv
processed CRESY.csv
processed SWIR.csv
processed TSCO.csv
processed DM.csv
processed APPH.csv
processed COP.csv
processed JWSM.csv
processed TSE.csv
processed CXE.csv
processed LOB.csv
processed ATSG.csv
processed GLP.csv
processed CELC.csv
out of range
processed CPHI.csv
processed SAFM.csv
processed DXF.csv
processed ZIP.csv
processed ALSK.csv
processed TPB.csv
processed THR.csv
processed WIX.csv
processed ALEX.csv
processed AEG.csv
processed ALLK.csv
processed ET.csv
processed LEJU.csv
processed DRRX.csv
processed GEF.csv
processed OXY.csv
processed ROK.csv
processed QDEL.csv
processed RGR.csv
processed

In [80]:
file = 'AMC.csv'

for index, row in df.iterrows():
    if '04:00:00' in row['human_dt']:
        #print(df.iloc[index+325]['human_dt'])
        if '09:2' in df.iloc[index+325]['human_dt']:
            print(df.iloc[index:index+325])
            
            
            premarket = df.iloc[index:index+325]
            window = df.iloc[index+325:index+340]
            
            date = row['human_dt'].split(' ')[0]
            
            high = window['high'].max()

            close = float(premarket.tail(1)['close'])

            change = round((high-close)/close*100)

            if change == 0:
                labels = 2
            elif change < -5:
                labels = 0
            elif change < 0:
                labels = 1
            elif change > 5:
                labels = 4
            elif change > 0:
                labels = 3

            count+=1
            
            name = f'cnn_premarket/{date}{file}'
            print(name)
            #market_open.to_csv(name)
            #new_df = pd.DataFrame([[name,labels]], columns = ['location', 'label'])
            #df = df.append(new_df,ignore_index=True)


In [ ]:
#processing into file to feed into custom dataset
'''
iterate through the daily ticker files
add technical indicators when opening
seperate each time period between 4-9:29 am
calculate for the following 15 minutes if the the high went down 5%, down less than 5%, stayed the same,
went up less than 5%, or went up more than 5%
save the file as a csv
add the file location and label in the csv that gets passed to the dataloader


'''

directory = 'minute_candlesticks/'

for file in os.listdir(directory):
    
    f = pd.read_csv(f'{directory}{file}')
    day = f['just_day'][0]
    f = f.drop(['Unnamed: 0','Unnamed: 0.1','just_day'],axis=1)
    premarket = f[f['human_dt'] < f'{day} 09:30:00']
    market_open = f[f['human_dt'] >= f'{day} 09:30:00']
    window = market_open[market_open['human_dt'] < f'{day} 09:46:00']

    nel = len(premarket)

    if nel >= 291:


        market_open = market_open.drop(['human_dt','datetime'],axis=1)
        market_open = market_open[:290]
        #values = torch.tensor(market_open.values)
        #value_lis.append(values)

        high = window['high'].max()
        #low = window['low'].min()

        close = float(premarket.tail(1)['close'])

        change = round((high-close)/close*100)

        if change == 0:
            labels = 2
        elif change < -5:
            labels = 0
        elif change < 0:
            labels = 1
        elif change > 5:
            labels = 4
        elif change > 0:
            labels = 3

        name = f'cnn_premarket/{folder}{file}'
        market_open.to_csv(name)
        new_df = pd.DataFrame([[name,labels]], columns = ['location', 'label'])
        df = df.append(new_df,ignore_index=True)


        print(f'{name} saved')

In [36]:
class StonksDataset(Dataset):
    def __init__(self, csv_file, root_dir, transform=None):
        self.annotations = pd.read_csv(csv_file)
        self.root_dir = root_dir
        self.transform = transform
        
    def __len__(self):
        return len(self.annotations)
    
    def __getitem__(self, index):
        img_path = os. path.join(self.annotations.iloc[index, 0])
        image = pd.read_csv(img_path)
        image = image.drop('Unnamed: 0',axis=1)

        y_label = torch.tensor(int(self.annotations.iloc[index, 1]))
    
        if self.transform:
            image = image.to_numpy()
            image = self.transform(image)
        return (image, y_label)

In [62]:
d = pd.read_csv('5min27.csv')
d

location  label
0     5min_premarket/2020-12-04CATB.csv      3
1     5min_premarket/2021-06-17CATB.csv      4
2     5min_premarket/2021-01-05CHEK.csv      4
3     5min_premarket/2021-01-06CHEK.csv      4
4     5min_premarket/2021-01-07CHEK.csv      3
...                                 ...    ...
2739   5min_premarket/2021-06-14ANY.csv      2
2740   5min_premarket/2021-02-03GSM.csv      4
2741  5min_premarket/2021-05-05PRPO.csv      3
2742  5min_premarket/2021-05-06PRPO.csv      3
2743  5min_premarket/2021-05-07PRPO.csv      2

[2744 rows x 2 columns]

In [57]:
dataset = StonksDataset(csv_file = '5min27.csv', root_dir='/', transform=transforms.ToTensor())
batch_size = 40
train_set, test_set = torch.utils.data.random_split(dataset, [2466,278])
train_loader = DataLoader(dataset=train_set, batch_size=batch_size, shuffle=True)
test_loader = DataLoader(dataset=test_set, batch_size=batch_size, shuffle=True)

In [58]:
import torch

model = torch.hub.load('pytorch/vision:v0.9.0', 'densenet201', pretrained=True)

Using cache found in /home/kyle/.cache/torch/hub/pytorch_vision_v0.9.0


In [59]:
model.features.conv0 = nn.Conv2d(1, 64, kernel_size=(5, 5), stride=(2, 2), padding=(5, 5), bias=False)

In [60]:
feature_extract=False
params_to_update = model.parameters()
print("Params to learn:")
if feature_extract:
    params_to_update = []
    for name,param in model.named_parameters():
        if param.requires_grad == True:
            params_to_update.append(param)
            print("\t",name)
else:
    for name,param in model.named_parameters():
        if param.requires_grad == True:
            print("\t",name)

optimizer = optim.SGD(params_to_update, lr=0.001, momentum=0.9)

criterion = nn.CrossEntropyLoss()

Params to learn:
	 features.conv0.weight
	 features.norm0.weight
	 features.norm0.bias
	 features.denseblock1.denselayer1.norm1.weight
	 features.denseblock1.denselayer1.norm1.bias
	 features.denseblock1.denselayer1.conv1.weight
	 features.denseblock1.denselayer1.norm2.weight
	 features.denseblock1.denselayer1.norm2.bias
	 features.denseblock1.denselayer1.conv2.weight
	 features.denseblock1.denselayer2.norm1.weight
	 features.denseblock1.denselayer2.norm1.bias
	 features.denseblock1.denselayer2.conv1.weight
	 features.denseblock1.denselayer2.norm2.weight
	 features.denseblock1.denselayer2.norm2.bias
	 features.denseblock1.denselayer2.conv2.weight
	 features.denseblock1.denselayer3.norm1.weight
	 features.denseblock1.denselayer3.norm1.bias
	 features.denseblock1.denselayer3.conv1.weight
	 features.denseblock1.denselayer3.norm2.weight
	 features.denseblock1.denselayer3.norm2.bias
	 features.denseblock1.denselayer3.conv2.weight
	 features.denseblock1.denselayer4.norm1.weight
	 features.de

In [61]:


epochs = 40
for epoch in range(epochs):
    
    train_loss = 0.0
    valid_loss = 0.0
    
    model.train()
    
    for images, labels in train_loader:
        
        optimizer.zero_grad()
        output = model.forward(images.float())
        loss = criterion(output, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()*images.size(0)

    model.eval()
    
    for data, target in test_loader:
        
        output = model(data.float())
        
    
        loss = criterion(output, target)
        valid_loss += loss.item()*data.size(0)
    
    train_loss = train_loss/len(train_loader.sampler)
    valid_loss = valid_loss/len(test_loader.sampler)
        
    print(f'Epoch: {epoch} Training Loss: {train_loss} valid: {valid_loss}')

Epoch: 0 Training Loss: 2.4102709210702105 valid: 1.4745511957209745
Epoch: 1 Training Loss: 0.9658660789572506 valid: 0.9966367311614881
Epoch: 2 Training Loss: 0.9863591516104928 valid: 1.3521252175886853
Epoch: 3 Training Loss: 0.9760395474097444 valid: 0.9844486173108328
Epoch: 4 Training Loss: 0.9446355685507101 valid: 0.9295232471802252
Epoch: 5 Training Loss: 0.9685948631769259 valid: 1.3463656057556757
Epoch: 6 Training Loss: 0.9223860142584844 valid: 1.1671526114717663
Epoch: 7 Training Loss: 0.9439672641123782 valid: 1.12849499982038
Epoch: 8 Training Loss: 0.9157935493087149 valid: 0.9232507416670271
Epoch: 9 Training Loss: 0.9468365533508524 valid: 0.9200687923019738
Epoch: 10 Training Loss: 0.9107928045958111 valid: 0.9405612066495332
Epoch: 11 Training Loss: 0.9556328939502063 valid: 1.1225939920480303
Epoch: 12 Training Loss: 0.9445463074288132 valid: 0.9002600625264559
Epoch: 13 Training Loss: 0.9567541990063583 valid: 1.1073597369434165
Epoch: 14 Training Loss: 0.93161

In [63]:
#alright then stock market, keep your secrets